
# plotting and manipulating icesat2 data from wei ji

Here I import icesat 2 data as an xarray and plot with hvplot

for an example of xarray in use https://github.com/weiji14/deepicedrain/blob/atl11_play/atl11_play.ipynb
to plot use https://hvplot.holoviz.org/

The area I import is the wrong area, though the methods are working

In [8]:

import rasterio as rio
import rasterio.mask
import fiona
import pandas as pd
import geopandas as gpd
from shapely.geometry import Polygon
import numpy as np
import os
import sys
import glob
import matplotlib.pyplot as plt
from scipy import interpolate
import xarray as xr
from shapely.geometry import Point
import hvplot.xarray  # noqa
import cartopy.crs as crs
import hvplot.pandas



In [9]:
path = "/Volumes/arc_02/REMOTE_SENSING/ICESAT2/kamb_atl11_subset.nc"


In [10]:
ds = xr.open_dataset(path, engine="h5netcdf")

In [11]:
ds

<xarray.Dataset>
Dimensions:                      (cycle_number: 6, poly_exponent_x: 8, poly_exponent_y: 8, ref_pt: 1512084)
Coordinates:
  * cycle_number                 (cycle_number) int64 1 2 3 4 5 6
  * poly_exponent_x              (poly_exponent_x) int64 1 0 2 1 0 3 2 1
  * poly_exponent_y              (poly_exponent_y) int64 0 1 0 1 2 0 1 2
  * ref_pt                       (ref_pt) int64 1533075 1533096 ... 1475760
    x                            (ref_pt) float64 ...
    y                            (ref_pt) float64 ...
Data variables:
    at_slope                     (ref_pt) float64 ...
    complex_surface_flag         (ref_pt) float64 ...
    curvature                    (ref_pt) float64 ...
    deg_x                        (ref_pt) float64 ...
    deg_y                        (ref_pt) float64 ...
    delta_time                   (ref_pt, cycle_number) timedelta64[ns] ...
    dem_h                        (ref_pt) float64 ...
    e_slope                      (ref_pt) float64 ...
    h_corr                       (ref_pt, cycle_number) float64 ...
    h_corr_sigma                 (ref_pt, cycle_number) float64 ...
    h_corr_sigma_systematic      (ref_pt, cycle_number) float64 ...
    latitude                     (ref_pt) float64 ...
    longitude                    (ref_pt) float64 ...
    misfit_RMS                   (ref_pt) float64 ...
    misfit_chi2r                 (ref_pt) float64 ...
    n_slope                      (ref_pt) float64 ...
    poly_coeffs                  (ref_pt, poly_exponent_x) float64 ...
    poly_coeffs_sigma            (ref_pt, poly_exponent_x) float64 ...
    quality_summary_corrected_h  (ref_pt, cycle_number) float64 ...
    quality_summary_ref_surf     (ref_pt) float64 ...
    rgt_azimuth                  (ref_pt) float64 ...
    slope_change_rate_x          (ref_pt) float64 ...
    slope_change_rate_x_sigma    (ref_pt) float64 ...
    slope_change_rate_y          (ref_pt) float64 ...
    slope_change_rate_y_sigma    (ref_pt) float64 ...
    utc_time                     (ref_pt, cycle_number) datetime64[ns] ...
    x_atc                        (ref_pt) float64 ...
    xt_slope                     (ref_pt) float64 ...
    y_atc                        (ref_pt) float64 ...
Attributes:
    poly_exponent_x:  [1 0 2 1 0 3 2 1]
    poly_exponent_y:  [0 1 0 1 2 0 1 2]
    slope_change_t0:  29548800

In [12]:
dd = ds.drop_dims(['poly_exponent_x','poly_exponent_y'])
df = dd.to_dataframe()
df.reset_index(inplace=True)
df.keys()

Index(['cycle_number', 'ref_pt', 'at_slope', 'complex_surface_flag',
       'curvature', 'deg_x', 'deg_y', 'delta_time', 'dem_h', 'e_slope',
       'h_corr', 'h_corr_sigma', 'h_corr_sigma_systematic', 'latitude',
       'longitude', 'misfit_RMS', 'misfit_chi2r', 'n_slope',
       'quality_summary_corrected_h', 'quality_summary_ref_surf',
       'rgt_azimuth', 'slope_change_rate_x', 'slope_change_rate_x_sigma',
       'slope_change_rate_y', 'slope_change_rate_y_sigma', 'utc_time', 'x',
       'x_atc', 'xt_slope', 'y', 'y_atc'],
      dtype='object')

In [13]:
df = ds[["h_corr", "utc_time"]].to_dataframe().reset_index()
df

cycle_number   ref_pt  h_corr utc_time              y              x
0                   1  1533075     NaN      NaT -425769.689841 -411541.944172
1                   1  1533096     NaN      NaT -426145.901999 -411696.860273
2                   1  1533099     NaN      NaT -426199.290451 -411718.824339
3                   1  1533114     NaN      NaT -426468.283852 -411829.371391
4                   1  1533144     NaN      NaT -427006.108985 -412051.579442
...               ...      ...     ...      ...            ...            ...
9072499             6  1475223     NaN      NaT -437192.503671 -421646.161754
9072500             6  1475391     NaN      NaT -435853.896597 -418673.864145
9072501             6  1475745     NaN      NaT -433035.290795 -412411.580006
9072502             6  1475748     NaN      NaT -433011.209731 -412358.367328
9072503             6  1475760     NaN      NaT -432915.288475 -412145.931245

[9072504 rows x 6 columns]

In [14]:
cycle_number = 4

df[df.cycle_number==cycle_number].hvplot.points(
    title=f"Elevation (metres) at Cycle {cycle_number}",
    x="x",
    y="y",
    c="h_corr",
    cmap="hsv",
    rasterize=True,
    hover=True,
)


:DynamicMap   []
   :Image   [x,y]   (h_corr)

In [15]:
dh = (ds.sel(cycle_number=6).h_corr-ds.sel(cycle_number=3).h_corr).to_dataframe().dropna()

In [31]:
dh.hvplot.points(
    title=f"Change in elevation from cycle 3 to cycle 6",
    x="x",
    y="y",
    c="h_corr",
    clim=(-0.3, 0.5),
    cmap="hsv",
    rasterize=True,
    hover=True
)

:DynamicMap   []
   :Image   [x,y]   (h_corr)

In [ ]:
# study_area = gpd.read_file('/Users/home/whitefar/DATA/FIELD_ANT_19/PRE_FIELD/KISRoutes/study_area_buffer.shp')
line_name='line7'
gdf = gpd.read_file("/Users/home/whitefar/DATA/FIELD_ANT_19/POST_FIELD/RES/PROCESSED_LINES_GISFILE/"
                        +line_name+".shp")
xmin,xmax = [gdf.geometry.x.to_numpy().min(),gdf.geometry.x.to_numpy().max()]
ymin,ymax = [gdf.geometry.y.to_numpy().min(),gdf.geometry.y.to_numpy().max()]
xlim = [xmin-1000, xmax]
ylim = [ymin-1000,ymax]
print(xlim,ylim)

In [ ]:
print(df.x.min(),df.x.max(),df.y.min(),df.y.max())

# out of bounds of what im trying to look at

Comparing to the study area, i realise that these plots are of a different area

In [ ]:
study_area = gpd.read_file('/Users/home/whitefar/DATA/FIELD_ANT_19/PRE_FIELD/KISRoutes/study_area_buffer.shp')
ge = study_area.geometry.iloc[0]
ge.bounds

In [ ]:
(-411054.19240523444,-739741.7702261859,-365489.6822096751,-699564.516934089)